# Assignment - Segmenting and Clustering Neighborhoods in Toronto

### Introduction

In the first part of this assignment, we will to extract postal codes from the following link:<br>
https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M

Only postal codes with an assigned borough will be consider for this Notebook.

### Import Libraries

First of all, let's import the necessary modules:

In [1]:
import requests # library to handle requests

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

#handle html data
!pip install bs4
from bs4 import BeautifulSoup

print('Libraries imported.')

Libraries imported.


### 1. Extract Postal Codes from Wiki


We use _Requests_ to get HTML code from the wiki page and _BeautifulSoup_ to handle the returned html data.

In [2]:
r = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')

soup = BeautifulSoup(r.text.replace('\n', ''), "html.parser") #replaces line break

postal_code_data = pd.DataFrame(columns=["Postal Code", "Borough", "Neighborhood"])

#finds the correct table based on its class
postal_code_table = soup.find("table", {"class": "wikitable"})

for row in postal_code_table.find("tbody").find_all("tr"):
    if not row.find_all("th"): #handle data only if no table head is found
        col = row.find_all("td")
        postal_code = col[0].text
        borough = col[1].text
        neighborhood = col[2].text
        
        if borough.upper() != 'NOT ASSIGNED':
            if neighborhood.upper() == 'NOT ASSIGNED':
                neighborhood = borough
            
            postal_code_data = postal_code_data.append({"Postal Code":postal_code, "Borough":borough, "Neighborhood":neighborhood}, ignore_index=True)

postal_code_data.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [3]:
postal_code_data.shape

(103, 3)

### 2. Add Latitude and Longitude (from CSV file)

Now, we get latitude and longitude from CSV File (http://cocl.us/Geospatial_data) to populate <i>postal_code_data</i>.

Download the CSV file to get the geo information:

In [4]:
csv_url = 'http://cocl.us/Geospatial_data'
df_csv = pd.read_csv(csv_url)
df_csv.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

Merge both dataframes based on the _Postal Code_ column:

In [5]:
postal_code_data = pd.merge(postal_code_data, df_csv, on=["Postal Code"])
postal_code_data.head(20)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   
12         M1C       Scarborough   
13         M3C        North York   
14         M4C         East York   
15         M5C  Downtown Toronto   
16         M6C              York   
17         M9C         Etobicoke   
18         M1E       Scarborough   
19         M4E      East Toronto   

                                         Neighborhood   Latitude  Longitude  
0                                           Parkwoods  43.753259 -79.329656  
1                                    Victoria Village  43.725882 -79.315572  
2                           Regent Park, Harbourfront  43.654260 -79.360636  
3                    Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4         Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
5             Islington Avenue, Humber Valley Village  43.667856 -79.532242  
6                                      Malvern, Rouge  43.806686 -79.194353  
7                                           Don Mills  43.745906 -79.352188  
8                     Parkview Hill, Woodbine Gardens  43.706397 -79.309937  
9                            Garden District, Ryerson  43.657162 -79.378937  
10                                          Glencairn  43.709577 -79.445073  
11  West Deane Park, Princess Gardens, Martin Grov...  43.650943 -79.554724  
12             Rouge Hill, Port Union, Highland Creek  43.784535 -79.160497  
13                                          Don Mills  43.725900 -79.340923  
14                                   Woodbine Heights  43.695344 -79.318389  
15                                     St. James Town  43.651494 -79.375418  
16                                 Humewood-Cedarvale  43.693781 -79.428191  
17  Eringate, Bloordale Gardens, Old Burnhamthorpe...  43.643515 -79.577201  
18                  Guildwood, Morningside, West Hill  43.763573 -79.188711  
19                                        The Beaches  43.676357 -79.293031

Although some neighborhoods are not unique in the data frame, they have different latitude and longitude coordinates, so we keep the data as it is.

In [6]:
# example of duplicated neighborhood
postal_code_data[postal_code_data["Neighborhood"] == "Don Mills"]

Postal Code     Borough Neighborhood   Latitude  Longitude
7          M3B  North York    Don Mills  43.745906 -79.352188
13         M3C  North York    Don Mills  43.725900 -79.340923

### 3. Explore and Cluster the Neighborhoods

Import necessary libraries for geolocation and map rendering:

In [7]:
#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


Solving environment: done

# All requested packages already installed.



### Create a map of Toronto

In [8]:
# get latitude and longitude basedo on an address
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create a map of Toronto with the latitude and longitude
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(postal_code_data['Latitude'], postal_code_data['Longitude'], postal_code_data['Borough'], postal_code_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Simplify Map

Let's simplify the map and segment and cluster only neighborhoods in _Downtown Toronto_.

In [9]:
downtown_toronto_data = postal_code_data[postal_code_data['Borough'] == 'Downtown Toronto'].reset_index(drop=True)
downtown_toronto_data.head()

Postal Code           Borough                                 Neighborhood  \
0         M5A  Downtown Toronto                    Regent Park, Harbourfront   
1         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
2         M5B  Downtown Toronto                     Garden District, Ryerson   
3         M5C  Downtown Toronto                               St. James Town   
4         M5E  Downtown Toronto                                  Berczy Park   

    Latitude  Longitude  
0  43.654260 -79.360636  
1  43.662301 -79.389494  
2  43.657162 -79.378937  
3  43.651494 -79.375418  
4  43.644771 -79.373306

In [10]:
downtown_toronto_data.shape

(19, 5)

### Create Map of Toronto with marks in Downtown Toronto borough

In [11]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=12)

for lat, lng, label in zip(downtown_toronto_data['Latitude'], downtown_toronto_data['Longitude'], downtown_toronto_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define Foursquare Credentials

API Foursquare credentials used in the URLs:

In [12]:
CLIENT_ID = '3DJMYO2CPIQ4U5JSEGR2BGQMA44CF5RTLEPFK0NWPRBIZ5W5' 
CLIENT_SECRET = 'LO5BK0IN5QD2HD0TYIHAA2XNKX4Y5CUFADSZRVJ33400PA5F'
VERSION = '20180605' # Foursquare API version

Let's explore a neighborhood of the data frame (I choose to set index 3):

In [13]:
index = 3

neighborhood_name = downtown_toronto_data.loc[index, 'Neighborhood']

# get geolocation of the neighborhood
neighborhood_latitude = downtown_toronto_data.loc[index, 'Latitude']
neighborhood_longitude = downtown_toronto_data.loc[index, 'Longitude']

print('Neighborhood: ', neighborhood_name)
print('Latitude: ', neighborhood_latitude)
print('Longitude: ', neighborhood_longitude)

Neighborhood:  St. James Town
Latitude:  43.6514939
Longitude:  -79.3754179


Now, let's get the top 100 venues in the neighborhood within  a radius of 500 meters:

In [14]:
limit = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    limit)

print(url)

https://api.foursquare.com/v2/venues/explore?&client_id=3DJMYO2CPIQ4U5JSEGR2BGQMA44CF5RTLEPFK0NWPRBIZ5W5&client_secret=LO5BK0IN5QD2HD0TYIHAA2XNKX4Y5CUFADSZRVJ33400PA5F&v=20180605&ll=43.6514939,-79.3754179&radius=500&limit=100


Define a function to get venue category:

In [15]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Clean JSON information and store it in a pandas data frame:

In [16]:
from pandas import json_normalize

# get response of URL request
r = requests.get(url).json()

venues = r['response']['groups'][0]['items']
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues = nearby_venues.loc[:, filtered_columns]

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]


# filter the category for each row
nearby_venues['categories'] = nearby_venues.apply(get_category_type, axis=1)

nearby_venues.head()

name           categories        lat        lng
0      Fahrenheit Coffee          Coffee Shop  43.652384 -79.372719
1  Gyu-Kaku Japanese BBQ  Japanese Restaurant  43.651422 -79.375047
2               Crepe TO             Creperie  43.650063 -79.374587
3      GEORGE Restaurant           Restaurant  43.653346 -79.374445
4          Hogtown Smoke           Food Truck  43.649287 -79.374689

How many venues were found in the neighborhood?

In [17]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

81 venues were returned by Foursquare.


### Explore  neighborhoods in Downtown Toronto

Now, we create a function to repeat the process with all neighborhoods in Downtown Toronto:

In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, limit=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit)
            
        # make the GET request
        r = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in r])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Run the function to process all neighborhoods, and store the returned information in a new dataframe

In [19]:
downtown_toronto_venues = getNearbyVenues(names=downtown_toronto_data['Neighborhood'],
                                   latitudes=downtown_toronto_data['Latitude'],
                                   longitudes=downtown_toronto_data['Longitude']
                                  )
downtown_toronto_venues.head()

Regent Park, Harbourfront
Queen's Park, Ontario Provincial Government
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Rosedale
Stn A PO Boxes
St. James Town, Cabbagetown
First Canadian Place, Underground city
Church and Wellesley


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront               43.65426              -79.360636   
1  Regent Park, Harbourfront               43.65426              -79.360636   
2  Regent Park, Harbourfront               43.65426              -79.360636   
3  Regent Park, Harbourfront               43.65426              -79.360636   
4  Regent Park, Harbourfront               43.65426              -79.360636   

                    Venue  Venue Latitude  Venue Longitude  \
0        Roselle Desserts       43.653447       -79.362017   
1           Tandem Coffee       43.653559       -79.361809   
2  Cooper Koo Family YMCA       43.653249       -79.358008   
3     Body Blitz Spa East       43.654735       -79.359874   
4          Impact Kitchen       43.656369       -79.356980   

        Venue Category  
0               Bakery  
1          Coffee Shop  
2  Distribution Center  
3                  Spa  
4           Restaurant

We can check how many venues were returned for each neighborhood:

In [20]:
downtown_toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            56   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Central Bay Street                                                     63   
Christie                                                               15   
Church and Wellesley                                                   80   
Commerce Court, Victoria Hotel                                        100   
First Canadian Place, Underground city                                100   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
Kensington Market, Chinatown, Grange Park                              66   
Queen's Park, Ontario Provincial Government                            30   
Regent Park, Harbourfront                                              42   
Richmond, Adelaide, King                                               93   
Rosedale                                                                4   
St. James Town                                                         81   
St. James Town, Cabbagetown                                            44   
Stn A PO Boxes                                                         98   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         33   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             56   
CN Tower, King and Spadina, Railway Lands, Harb...                      16   
Central Bay Street                                                      63   
Christie                                                                15   
Church and Wellesley                                                    80   
Commerce Court, Victoria Hotel                                         100   
First Canadian Place, Underground city                                 100   
Garden District, Ryerson                                               100   
Harbourfront East, Union Station, Toronto Islands                      100   
Kensington Market, Chinatown, Grange Park                               66   
Queen's Park, Ontario Provincial Government                             30   
Regent Park, Harbourfront                                               42   
Richmond, Adelaide, King                                                93   
Rosedale                                                                 4   
St. James Town                                                          81   
St. James Town, Cabbagetown                                             44   
Stn A PO Boxes                                                          98   
Toronto Dominion Centre, Design Exchange                               100   
University of Toronto, Harbord                                          33   

                                                    Venue  Venue Latitude  \
Neighborhood                                                                
Berczy Park                                            56              56   
CN Tower, King and Spadina, Railway Lands, Harb...     16              16   
Central Bay Street                                     63              63   
Christie                                               15              15   
Church and Wellesley                                   80              80   
Commerce Court, Victoria Hotel                        100             100   
First Canadian Place, Underground city                100             100   
Garden District, Ryerson                              100             100   
Harbourfront East, Union 

### Analyze Each Neighborhood

In [21]:
#create a new dataframe, converting categories into indicator variables
# one hot encoding
downtown_toronto_onehot = pd.get_dummies(downtown_toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
downtown_toronto_onehot['Neighborhood'] = downtown_toronto_venues['Neighborhood'] 

downtown_toronto_onehot

Airport  Airport Food Court  Airport Lounge  Airport Service  \
0           0                   0               0                0   
1           0                   0               0                0   
2           0                   0               0                0   
3           0                   0               0                0   
4           0                   0               0                0   
5           0                   0               0                0   
6           0                   0               0                0   
7           0                   0               0                0   
8           0                   0               0                0   
9           0                   0               0                0   
10          0                   0               0                0   
11          0                   0               0                0   
12          0                   0               0                0   
13          0                   0               0                0   
14          0                   0               0                0   
15          0                   0               0                0   
16          0                   0               0                0   
17          0                   0               0                0   
18          0                   0               0                0   
19          0                   0               0                0   
20          0                   0               0                0   
21          0                   0               0                0   
22          0                   0               0                0   
23          0                   0               0                0   
24          0                   0               0                0   
25          0                   0               0                0   
26          0                   0               0                0   
27          0                   0               0                0   
28          0                   0               0                0   
29          0                   0               0                0   
30          0                   0               0                0   
31          0                   0               0                0   
32          0                   0               0                0   
33          0                   0               0                0   
34          0                   0               0                0   
35          0                   0               0                0   
36          0                   0               0                0   
37          0                   0               0                0   
38          0                   0               0                0   
39          0                   0               0                0   
40          0                   0               0                0   
41          0                   0               0                0   
42          0                   0               0                0   
43          0                   0               0                0   
44          0                   0               0                0   
45          0                   0               0                0   
46          0                   0               0                0   
47          0                   0               0                0   
48          0                   0               0                0   
49          0                   0               0                0   
50          0                   0               0                0   
51          0                   0               0                0   
52          0                   0               0                0   
53          0                   0               0                0   
54          0                   0               0                0   
55          0                   0               0                0   
56          0   

Let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category:

In [22]:
downtown_toronto_grouped = downtown_toronto_onehot.groupby('Neighborhood').mean().reset_index()
downtown_toronto_grouped

Neighborhood  Airport  \
0                                         Berczy Park   0.0000   
1   CN Tower, King and Spadina, Railway Lands, Har...   0.0625   
2                                  Central Bay Street   0.0000   
3                                            Christie   0.0000   
4                                Church and Wellesley   0.0000   
5                      Commerce Court, Victoria Hotel   0.0000   
6              First Canadian Place, Underground city   0.0000   
7                            Garden District, Ryerson   0.0000   
8   Harbourfront East, Union Station, Toronto Islands   0.0000   
9           Kensington Market, Chinatown, Grange Park   0.0000   
10        Queen's Park, Ontario Provincial Government   0.0000   
11                          Regent Park, Harbourfront   0.0000   
12                           Richmond, Adelaide, King   0.0000   
13                                           Rosedale   0.0000   
14                                     St. James Town   0.0000   
15                        St. James Town, Cabbagetown   0.0000   
16                                     Stn A PO Boxes   0.0000   
17           Toronto Dominion Centre, Design Exchange   0.0000   
18                     University of Toronto, Harbord   0.0000   

    Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0               0.0000           0.000           0.0000             0.000   
1               0.0625           0.125           0.1875             0.125   
2               0.0000           0.000           0.0000             0.000   
3               0.0000           0.000           0.0000             0.000   
4               0.0000           0.000           0.0000             0.000   
5               0.0000           0.000           0.0000             0.000   
6               0.0000           0.000           0.0000             0.000   
7               0.0000           0.000           0.0000             0.000   
8               0.0000           0.000           0.0000             0.000   
9               0.0000           0.000           0.0000             0.000   
10              0.0000           0.000           0.0000             0.000   
11              0.0000           0.000           0.0000             0.000   
12              0.0000           0.000           0.0000             0.000   
13              0.0000           0.000           0.0000             0.000   
14              0.0000           0.000           0.0000             0.000   
15              0.0000           0.000           0.0000             0.000   
16              0.0000           0.000           0.0000             0.000   
17              0.0000           0.000           0.0000             0.000   
18              0.0000           0.000           0.0000             0.000   

    American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0              0.000000      0.000000      0.00     0.017857    0.000000   
1              0.000000      0.000000      0.00     0.000000    0.000000   
2              0.000000      0.000000      0.00     0.000000    0.015873   
3              0.000000      0.000000      0.00     0.000000    0.000000   
4              0.012500      0.000000      0.00     0.000000    0.000000   
5              0.040000      0.000000      0.00     0.010000    0.000000   
6              0.030000      0.000000      0.00     0.010000    0.000000   
7              0.000000      0.000000      0.00     0.010000    0.000000   
8              0.000000      0.000000      0.05     0.010000    0.000000   
9              0.000000      0.000000      0.00     0.000000    0.000000   
10             0.000000      0.000000      0.00     0.000000    0.000000   
11             0.000000      0.023810      0.00     0.023810    0.000000   
12             0.021505      0.000000      0.00     0.010753    0.010753   
13             0.000000      0.000000      0.00     0.000000    0.000000   
14             0.037037      0.000000  

Let's list Top 5 Venues of each neighborhoods:

In [23]:
num_top_venues = 5

for hood in downtown_toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = downtown_toronto_grouped[downtown_toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
            venue  freq
0     Coffee Shop  0.09
1    Cocktail Bar  0.07
2          Bakery  0.04
3  Farmers Market  0.04
4        Beer Bar  0.04


----CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport----
              venue  freq
0   Airport Service  0.19
1    Airport Lounge  0.12
2  Airport Terminal  0.12
3           Airport  0.06
4     Boat or Ferry  0.06


----Central Bay Street----
                venue  freq
0         Coffee Shop  0.17
1      Sandwich Place  0.06
2  Italian Restaurant  0.05
3                Café  0.05
4         Salad Place  0.03


----Christie----
           venue  freq
0  Grocery Store  0.27
1           Café  0.20
2           Park  0.13
3    Coffee Shop  0.07
4      Nightclub  0.07


----Church and Wellesley----
                 venue  freq
0          Coffee Shop  0.09
1  Japanese Restaurant  0.06
2     Sushi Restaurant  0.06
3              Gay Bar  0.04
4           Restaurant  0.04


--

Let's create a function to sort venues in descending order:

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Store storted venues in a data frame:

In [25]:
import numpy as np

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = downtown_toronto_grouped['Neighborhood']

for ind in np.arange(downtown_toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(downtown_toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
2                                 Central Bay Street           Coffee Shop   
3                                           Christie         Grocery Store   
4                               Church and Wellesley           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Cocktail Bar                Bakery        Farmers Market   
1        Airport Lounge      Airport Terminal               Airport   
2        Sandwich Place    Italian Restaurant                  Café   
3                  Café                  Park           Coffee Shop   
4   Japanese Restaurant      Sushi Restaurant               Gay Bar   

  5th Most Common Venue 6th Most Common Venue     7th Most Common Venue  \
0              Beer Bar           Cheese Shop        Seafood Restaurant   
1         Boat or Ferry   Rental Car Location               Coffee Shop   
2           Salad Place          Burger Joint           Bubble Tea Shop   
3             Nightclub            Restaurant               Candy Store   
4            Restaurant                 Hotel  Mediterranean Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Restaurant   Japanese Restaurant         Breakfast Spot  
1      Sculpture Garden              Boutique                  Plane  
2     French Restaurant   Japanese Restaurant      Indian Restaurant  
3            Baby Store    Italian Restaurant                Airport  
4           Men's Store  Fast Food Restaurant                    Pub

### Cluster Neighborhoods

Run k-means to cluster the neighborhood into 5 clusters:

In [26]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

kclusters = 5

downtown_toronto_grouped_clustering = downtown_toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(downtown_toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 3, 4, 2, 0, 0, 0, 0, 0, 0], dtype=int32)

 Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood:

In [27]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

downtown_toronto_merged = downtown_toronto_data

# merge dataframes to add latitude/longitude for each neighborhood
downtown_toronto_merged = downtown_toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

downtown_toronto_merged.head()

Postal Code           Borough                                 Neighborhood  \
0         M5A  Downtown Toronto                    Regent Park, Harbourfront   
1         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
2         M5B  Downtown Toronto                     Garden District, Ryerson   
3         M5C  Downtown Toronto                               St. James Town   
4         M5E  Downtown Toronto                                  Berczy Park   

    Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  43.654260 -79.360636               4           Coffee Shop   
1  43.662301 -79.389494               4           Coffee Shop   
2  43.657162 -79.378937               0        Clothing Store   
3  43.651494 -79.375418               0                  Café   
4  43.644771 -79.373306               0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Park                Bakery        Breakfast Spot   
1      Sushi Restaurant           Yoga Studio                   Bar   
2           Coffee Shop   Japanese Restaurant       Bubble Tea Shop   
3           Coffee Shop   American Restaurant             Gastropub   
4          Cocktail Bar                Bakery        Farmers Market   

  5th Most Common Venue      6th Most Common Venue 7th Most Common Venue  \
0               Theater                       Café                   Pub   
1                 Diner                   Creperie   Distribution Center   
2                 Hotel  Middle Eastern Restaurant    Italian Restaurant   
3          Cocktail Bar                 Restaurant        Lingerie Store   
4              Beer Bar                Cheese Shop    Seafood Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Electronics Store               Brewery         Chocolate Shop  
1                  Park    College Auditorium         Sandwich Place  
2        Cosmetics Shop                  Café         Lingerie Store  
3                   Gym        Farmers Market    Moroccan Restaurant  
4            Restaurant   Japanese Restaurant         Breakfast Spot

Now, we create a map to visualize the resulting clusters:

In [28]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(downtown_toronto_merged['Latitude'], downtown_toronto_merged['Longitude'], downtown_toronto_merged['Neighborhood'], downtown_toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### And finally, analyze each cluster so we can check the differences between them

Cluster 1:

In [29]:
downtown_toronto_merged.loc[downtown_toronto_merged['Cluster Labels'] == 0, downtown_toronto_merged.columns[[2] + list(range(5, downtown_toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
2                            Garden District, Ryerson               0   
3                                      St. James Town               0   
4                                         Berczy Park               0   
7                            Richmond, Adelaide, King               0   
8   Harbourfront East, Union Station, Toronto Islands               0   
9            Toronto Dominion Centre, Design Exchange               0   
10                     Commerce Court, Victoria Hotel               0   
11                     University of Toronto, Harbord               0   
12          Kensington Market, Chinatown, Grange Park               0   
15                                     Stn A PO Boxes               0   
16                        St. James Town, Cabbagetown               0   
17             First Canadian Place, Underground city               0   
18                               Church and Wellesley               0   

            1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
2                  Clothing Store           Coffee Shop   Japanese Restaurant   
3                            Café           Coffee Shop   American Restaurant   
4                     Coffee Shop          Cocktail Bar                Bakery   
7                     Coffee Shop                  Café            Restaurant   
8                     Coffee Shop              Aquarium                 Hotel   
9                     Coffee Shop                 Hotel                  Café   
10                    Coffee Shop            Restaurant                  Café   
11                           Café                   Bar             Bookstore   
12  Vegetarian / Vegan Restaurant                  Café           Coffee Shop   
15                    Coffee Shop          Cocktail Bar    Seafood Restaurant   
16                    Coffee Shop                Bakery            Restaurant   
17                    Coffee Shop                  Café                 Hotel   
18                    Coffee Shop   Japanese Restaurant      Sushi Restaurant   

   4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
2        Bubble Tea Shop                 Hotel  Middle Eastern Restaurant   
3              Gastropub          Cocktail Bar                 Restaurant   
4         Farmers Market              Beer Bar                Cheese Shop   
7         Clothing Store         Deli / Bodega                        Gym   
8                   Café    Italian Restaurant        Sporting Goods Shop   
9    Japanese Restaurant    Seafood Restaurant                Salad Place   
10                 Hotel    Italian Restaurant        American Restaurant   
11   Japanese Restaurant                Bakery             Sandwich Place   
12                Bakery                   Bar      Vietnamese Restaurant   
15              Beer Bar   Japanese Restaurant         Italian Restaurant   
16                  Café    Italian Restaurant                Pizza Place   
17   Japanese Restaurant            Restaurant                        Gym   
18               Gay Bar            Restaurant                      Hotel   

       7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
2         Italian Restaurant        Cosmetics Shop                   Café   
3             Lingerie Store                   Gym         Farmers Market   
4         Seafood Restaurant            Restaurant    Japanese Restaurant   
7            Thai Restaurant                Bakery           Concert Hall   
8                    Brewery        Scenic Lookout    Fried Chicken Joint   
9                 Restaurant   American Restaurant     Italian Restaurant   
10                       Gym          Cocktail Bar          Deli / Bodega   
11         French Restaurant           Coffee Shop  College Arts Building   
12        Mexican Restaurant         Grocery Store                   Park   
15                      Café      

Cluster 2:

In [30]:
downtown_toronto_merged.loc[downtown_toronto_merged['Cluster Labels'] == 1, downtown_toronto_merged.columns[[2] + list(range(5, downtown_toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
14     Rosedale               1                  Park            Playground   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
14                 Trail               Airport                Museum   

   6th Most Common Venue 7th Most Common Venue      8th Most Common Venue  \
14           Men's Store    Mexican Restaurant  Middle Eastern Restaurant   

   9th Most Common Venue      10th Most Common Venue  
14    Miscellaneous Shop  Modern European Restaurant

Cluster 3:

In [31]:
downtown_toronto_merged.loc[downtown_toronto_merged['Cluster Labels'] == 2, downtown_toronto_merged.columns[[2] + list(range(5, downtown_toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
6     Christie               2         Grocery Store                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6                  Park           Coffee Shop             Nightclub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6            Restaurant           Candy Store            Baby Store   

  9th Most Common Venue 10th Most Common Venue  
6    Italian Restaurant                Airport

Cluster 4:

In [32]:
downtown_toronto_merged.loc[downtown_toronto_merged['Cluster Labels'] == 3, downtown_toronto_merged.columns[[2] + list(range(5, downtown_toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
13  CN Tower, King and Spadina, Railway Lands, Har...               3   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
13       Airport Service        Airport Lounge      Airport Terminal   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
13               Airport         Boat or Ferry   Rental Car Location   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
13           Coffee Shop      Sculpture Garden              Boutique   

   10th Most Common Venue  
13                  Plane

Cluster 5:

In [33]:
downtown_toronto_merged.loc[downtown_toronto_merged['Cluster Labels'] == 4, downtown_toronto_merged.columns[[2] + list(range(5, downtown_toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
0                    Regent Park, Harbourfront               4   
1  Queen's Park, Ontario Provincial Government               4   
5                           Central Bay Street               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Coffee Shop                  Park                Bakery   
1           Coffee Shop      Sushi Restaurant           Yoga Studio   
5           Coffee Shop        Sandwich Place    Italian Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Breakfast Spot               Theater                  Café   
1                   Bar                 Diner              Creperie   
5                  Café           Salad Place          Burger Joint   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                   Pub     Electronics Store               Brewery   
1   Distribution Center                  Park    College Auditorium   
5       Bubble Tea Shop     French Restaurant   Japanese Restaurant   

  10th Most Common Venue  
0         Chocolate Shop  
1         Sandwich Place  
5      Indian Restaurant